# Instalação de pacotes

In [243]:
# !pip install -U ydata-profiling

In [248]:
!pip install sdv

  Using cached scikit_learn-1.5.2-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (13 kB)
  Using cached threadpoolctl-3.5.0-py3-none-any.whl.metadata (13 kB)
  Using cached nvidia_cudnn_cu12-9.1.0.70-py3-none-manylinux2014_x86_64.whl.metadata (1.6 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 154.0/154.0 kB 371.5 kB/s eta 0:00:00m eta 0:00:010:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 139.2/139.2 kB 356.6 kB/s eta 0:00:00 kB/s eta 0:00:01:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.2/13.2 MB 2.7 MB/s eta 0:00:00m eta 0:00:010:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 52.4/52.4 kB 498.0 kB/s eta 0:00:0036m0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.8/66.8 kB 127.1 kB/s eta 0:00:001m7.0 MB/s eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.1/175.1 kB 784.6 kB/s eta 0:00:00 eta 0:00:010:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.9/1.9 MB 2.4 MB/s eta 0:00:00m eta 0:00:010:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

# Importação de depedências

In [1]:
import pandas as pd
from typing import Optional

In [2]:
import hashlib
import uuid


In [189]:
from ydata_profiling import ProfileReport

# Préprocessamento

In [8]:
ds =  pd.read_csv("datsetPeqsuisaFinal.csv", encoding='utf-8',sep=",")

FileNotFoundError: [Errno 2] No such file or directory: 'datsetPeqsuisaFinal.csv'

Anonimização dos dados

In [ ]:

class GerenciadorAnonimizacao:
    def __init__(self, email: Optional[str] = None):
        """
        Inicializa o gerenciador de anonimização com um e-mail opcional.
        """
        self.email = email

    def set_email(self, email: str):
        """
        Define o e-mail a ser anonimizado.
        """
        self.email = email

    def anonimizar_uuid(self) -> Optional[str]:
        """
        Anonimiza o e-mail usando UUID (namespace DNS).
        """
        if self.email and pd.notnull(self.email):
            return str(uuid.uuid5(uuid.NAMESPACE_DNS, self.email))
        return None

    def anonimizar_sha(self) -> Optional[str]:
        """
        Anonimiza o e-mail usando SHA-256.
        """
        if self.email and pd.notnull(self.email):
            return hashlib.sha256(self.email.encode('utf-8')).hexdigest()
        return None

    @staticmethod
    def anonimizar_email_legivel(email: str) -> Optional[str]:
        """
        Anonimiza o e-mail de forma legível, preservando o domínio.
        """
        try:
            local, domain = email.split('@')
            anonymized_local = (
                local[0] + '*' * (len(local) - 2) + local[-1] if len(local) > 2 else '*' * len(local)
            )
            return anonymized_local + '@' + domain
        except:
            return email  # Retorna o dado original se não for um e-mail válido


In [ ]:
def aplicarSha(email):
    gerenciador = GerenciadorAnonimizacao(email=email)
    return gerenciador.anonimizar_sha()

def aplicarUuid(email):
    gerenciador = GerenciadorAnonimizacao(email=email)
    return gerenciador.anonimizar_uuid()

def aplicarAnonimizacaoLegivel(email):
    return GerenciadorAnonimizacao.anonimizar_email_legivel(email)
    
    

In [ ]:
# Aplicar anonimização à coluna de e-mail
opcaoAnonimizacao = "UUID"
if 'Endereço de e-mail' in ds.columns:
    match opcaoAnonimizacao:
        case "UUID":
            ds['Endereço de e-mail'] = ds['Endereço de e-mail'].apply(aplicarUuid)

        case "SHA256":
            ds['Endereço de e-mail'] = ds['Endereço de e-mail'].apply(aplicarSha)
            
        case "LEGIVEL":
            ds['Endereço de e-mail'] =  ds['Endereço de e-mail'].apply(aplicarAnonimizacaoLegivel)
            


In [ ]:
ds

In [ ]:
ds.to_csv("datsetPeqsuisaAnonimizado.csv")

# Importação de datset Anonimizado

In [4]:
dsAnonimizado = pd.read_csv("datsetPeqsuisaAnonimizado.csv")

In [5]:
dsAnonimizado.drop(columns=['Unnamed: 0'], inplace=True)

In [16]:
dsAnonimizado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 51 columns):
 #   Column                                                                                                                                                                                                  Non-Null Count  Dtype  
---  ------                                                                                                                                                                                                  --------------  -----  
 0   Carimbo de data/hora                                                                                                                                                                                    57 non-null     object 
 1   Endereço de e-mail                                                                                                                                                                                      57 no

In [18]:
dsAnonimizado.keys()

Index(['Carimbo de data/hora', 'Endereço de e-mail', 'Qual é a sua idade?',
       'Gênero', 'Quais plataformas de mídia social você costuma usar?',
       'Cidade onde Mora', 'Sexo', 'Está empregado',
       'Já foi diagnosticado por um profissional com algum dos itens: [Nenhum]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Depressão]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Ansiedade]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Estresse]',
       'Já foi diagnosticado por um profissional com algum dos itens: [TDAH]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno Bipolar]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno de ansiedade social :]',
       'Já foi diagnosticado por um profissional com algum dos itens: [Fobia de Perda de Conexão ( Ansiedade relacionada à ausência de acesso ao celular ou redes sociais, causando angústi

In [20]:
representacao = {titulo: idx for idx, titulo in enumerate(dsAnonimizado.keys())}

In [22]:
representacao 

{'Carimbo de data/hora': 0,
 'Endereço de e-mail': 1,
 'Qual é a sua idade?': 2,
 'Gênero': 3,
 'Quais plataformas de mídia social você costuma usar?': 4,
 'Cidade onde Mora': 5,
 'Sexo': 6,
 'Está empregado': 7,
 'Já foi diagnosticado por um profissional com algum dos itens: [Nenhum]': 8,
 'Já foi diagnosticado por um profissional com algum dos itens: [Depressão]': 9,
 'Já foi diagnosticado por um profissional com algum dos itens: [Ansiedade]': 10,
 'Já foi diagnosticado por um profissional com algum dos itens: [Estresse]': 11,
 'Já foi diagnosticado por um profissional com algum dos itens: [TDAH]': 12,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno Bipolar]': 13,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno de ansiedade social :]': 14,
 'Já foi diagnosticado por um profissional com algum dos itens: [Fobia de Perda de Conexão ( Ansiedade relacionada à ausência de acesso ao celular ou redes sociais, causando angústia e desconf

In [24]:
df = dsAnonimizado.copy()

In [26]:
df.columns = range(len(df.columns))

In [28]:
df

0                                     1         2   \
0   16/11/2024 08:50:05  2903def3-aa2f-5bf3-8d43-f9396e259be8        41   
1   16/11/2024 08:56:56  52101e6a-ca49-5844-a546-155aa08bf771        33   
2   16/11/2024 08:58:00  0135da91-4288-5475-8a7d-c06ac32e157d        51   
3   16/11/2024 08:58:23  ef094ef4-c311-52ab-994b-a5e2943c8c04        37   
4   16/11/2024 09:04:14  4fe3cb6d-8d9f-5fdd-87fa-13481495a0c4        30   
5   16/11/2024 09:08:52  8f30b1fa-511d-5044-948d-268c86cb55df        36   
6   16/11/2024 09:12:53  844ab66e-8e20-57df-92c1-2ecb27388676        37   
7   16/11/2024 09:19:18  da896799-9ea2-5e91-ad37-3a9bf6a5eea9        34   
8   16/11/2024 09:21:15  76f728ad-95de-5906-81cf-682fcbf25c03        33   
9   16/11/2024 09:25:20  3f123bb8-6b37-58e8-bccd-035231c8a49c        44   
10  16/11/2024 09:28:39  39c3fb67-2006-5cfc-8c6e-92b9638e01c3        40   
11  16/11/2024 09:44:19  bbb15780-cc69-5b92-9733-a5b7ac49cf84        43   
12  16/11/2024 09:57:47  5a94a0af-1f02-518c-9d97-4d84c2b4a238        59   
13  16/11/2024 09:58:19  9e19ad96-acaf-5f4c-8d6f-68fd689b4a28        34   
14  16/11/2024 10:35:56  7e960c6a-1666-530f-8352-b2b57322a37b        37   
15  16/11/2024 10:43:45  89af1ea9-ed96-5a12-ac1f-569141e4dd3b        33   
16  16/11/2024 10:44:43  5553edd9-4ffa-5f9e-b23c-0ec586faac92        33   
17  16/11/2024 10:49:57  d6619a23-2eb7-5c97-8f3a-5d1ed07daadb        40   
18  16/11/2024 10:58:30  ee378c51-702f-5e5f-90d7-8929e279a999        33   
19  16/11/2024 10:59:04  6180a5a7-24b2-578d-a9c8-6fe019950127        36   
20  16/11/2024 11:28:07  b6c4ce6b-fa2c-58b1-902f-5a35821091ab        34   
21  16/11/2024 11:28:45  2c35c15d-09d5-51ff-b647-2dbc1bc31b32        54   
22  16/11/2024 11:42:43  7d3aed80-5b84-551e-88a5-e78768c61784        43   
23  16/11/2024 11:42:45  4935d0e4-ed00-523c-8d16-9dcc2273d6c3        47   
24  16/11/2024 11:52:04  66e637f0-f501-5faa-bd9d-3c32504b27f2        28   
25  16/11/2024 11:56:56  cecd8d29-012e-5dbf-aad7-61887822eba5        24   
26  16/11/2024 12:02:21  92f6a363-67a4-5b0b-a2c8-83fdec015808        40   
27  16/11/2024 12:06:47  efd75239-cc3e-59c0-97e1-400a60b59516        46   
28  16/11/2024 12:17:28  28f1561e-9c1b-5fae-a52d-1173b3285da2        48   
29  16/11/2024 12:20:31  d4b48127-c1df-5ef8-93a1-e7aa4250a15a        59   
30  16/11/2024 12:29:09  d5b52350-81cf-50a5-b462-85c05c01ebec        25   
31  16/11/2024 12:32:33  3138d431-cc7b-59f3-bdcf-10cd82c55545        36   
32  16/11/2024 12:48:11  1c6101fe-3808-53d7-a804-c91dcc7e32d8        40   
33  16/11/2024 12:54:04  08d8653a-5fa3-55b5-a9cb-f658bbc46463        42   
34  16/11/2024 13:13:56  1982ad6f-0db0-5ae3-8090-1fe0b82d7e21        41   
35  16/11/2024 13:55:05  4e25cc7a-f744-5c18-b82d-7dd234072395        41   
36  16/11/2024 15:47:26  9e502950-aef7-568c-80d3-b3c6d62db398        55   
37  16/11/2024 16:42:12  f3d1fcbe-61f5-56c0-ab76-dce7d4f98e13        48   
38  16/11/2024 18:30:43  31603a5d-2550-5586-9d88-abb9ff7ccd76        43   
39  16/11/2024 18:37:09  24c588c8-7897-5fef-b675-8921af1aab92       NaN   
40  16/11/2024 18:53:28  26644736-c2d9-52c6-8e2b-c32fbcec3412        19   
41  16/11/2024 20:37:51  d754d3a7-5ebc-5c5d-bdac-2a84562603ff        36   
42  17/11/2024 00:03:23  fedb0c5f-d552-552b-8124-bfeee790c7c4        36   
43  17/11/2024 10:18:27  3d4443e4-6a96-584b-b941-39eebbd6f957        47   
44  17/11/2024 11:37:14  693b1e30-a43d-5498-821d-668a0d0925b2        45   
45  17/11/2024 14:24:30  3a08cfcd-5ef7-5350-922c-403904b3d1c0        55   
46  17/11/2024 17:02:37  040ce340-fde4-50f0-95d6-80a524b8adb7        59   
47  17/11/2024 19:21:17  fcc38cc1-b101-5ee5-9548-3554022421c7        33   
48  17/11/2024 22:40:50  6baadd18-584e-5f22-839b-2d811106210f        37   
49  17/11/2024 23:03:37  6bed0452-65a6-5d7b-a207-05b75e464ffc        60   
50  18/11/2024 13:16:10  fc2f505c-35e2-5978-96e3-a422b6eb1934  51 anos    
51  18/11/2024 13:17:51  72bda606-2554-5fe4-aac7-a9df524fb04e        31   
52  18/11/2024 13:18:08  40500e35-5efe-5b8a-ba

In [30]:
colunas_para_substituir = [8,9,10,11,12,13,14,15,16,17,18,40,41,42,43,44,45,46,47,48,49,50]

In [32]:
df[colunas_para_substituir]=df[colunas_para_substituir].replace("Coluna 1",1)
df[colunas_para_substituir]= df[colunas_para_substituir].fillna(0)

/tmp/ipykernel_6332/4145260323.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df[colunas_para_substituir]=df[colunas_para_substituir].replace("Coluna 1",1)


In [34]:
df

0                                     1         2   \
0   16/11/2024 08:50:05  2903def3-aa2f-5bf3-8d43-f9396e259be8        41   
1   16/11/2024 08:56:56  52101e6a-ca49-5844-a546-155aa08bf771        33   
2   16/11/2024 08:58:00  0135da91-4288-5475-8a7d-c06ac32e157d        51   
3   16/11/2024 08:58:23  ef094ef4-c311-52ab-994b-a5e2943c8c04        37   
4   16/11/2024 09:04:14  4fe3cb6d-8d9f-5fdd-87fa-13481495a0c4        30   
5   16/11/2024 09:08:52  8f30b1fa-511d-5044-948d-268c86cb55df        36   
6   16/11/2024 09:12:53  844ab66e-8e20-57df-92c1-2ecb27388676        37   
7   16/11/2024 09:19:18  da896799-9ea2-5e91-ad37-3a9bf6a5eea9        34   
8   16/11/2024 09:21:15  76f728ad-95de-5906-81cf-682fcbf25c03        33   
9   16/11/2024 09:25:20  3f123bb8-6b37-58e8-bccd-035231c8a49c        44   
10  16/11/2024 09:28:39  39c3fb67-2006-5cfc-8c6e-92b9638e01c3        40   
11  16/11/2024 09:44:19  bbb15780-cc69-5b92-9733-a5b7ac49cf84        43   
12  16/11/2024 09:57:47  5a94a0af-1f02-518c-9d97-4d84c2b4a238        59   
13  16/11/2024 09:58:19  9e19ad96-acaf-5f4c-8d6f-68fd689b4a28        34   
14  16/11/2024 10:35:56  7e960c6a-1666-530f-8352-b2b57322a37b        37   
15  16/11/2024 10:43:45  89af1ea9-ed96-5a12-ac1f-569141e4dd3b        33   
16  16/11/2024 10:44:43  5553edd9-4ffa-5f9e-b23c-0ec586faac92        33   
17  16/11/2024 10:49:57  d6619a23-2eb7-5c97-8f3a-5d1ed07daadb        40   
18  16/11/2024 10:58:30  ee378c51-702f-5e5f-90d7-8929e279a999        33   
19  16/11/2024 10:59:04  6180a5a7-24b2-578d-a9c8-6fe019950127        36   
20  16/11/2024 11:28:07  b6c4ce6b-fa2c-58b1-902f-5a35821091ab        34   
21  16/11/2024 11:28:45  2c35c15d-09d5-51ff-b647-2dbc1bc31b32        54   
22  16/11/2024 11:42:43  7d3aed80-5b84-551e-88a5-e78768c61784        43   
23  16/11/2024 11:42:45  4935d0e4-ed00-523c-8d16-9dcc2273d6c3        47   
24  16/11/2024 11:52:04  66e637f0-f501-5faa-bd9d-3c32504b27f2        28   
25  16/11/2024 11:56:56  cecd8d29-012e-5dbf-aad7-61887822eba5        24   
26  16/11/2024 12:02:21  92f6a363-67a4-5b0b-a2c8-83fdec015808        40   
27  16/11/2024 12:06:47  efd75239-cc3e-59c0-97e1-400a60b59516        46   
28  16/11/2024 12:17:28  28f1561e-9c1b-5fae-a52d-1173b3285da2        48   
29  16/11/2024 12:20:31  d4b48127-c1df-5ef8-93a1-e7aa4250a15a        59   
30  16/11/2024 12:29:09  d5b52350-81cf-50a5-b462-85c05c01ebec        25   
31  16/11/2024 12:32:33  3138d431-cc7b-59f3-bdcf-10cd82c55545        36   
32  16/11/2024 12:48:11  1c6101fe-3808-53d7-a804-c91dcc7e32d8        40   
33  16/11/2024 12:54:04  08d8653a-5fa3-55b5-a9cb-f658bbc46463        42   
34  16/11/2024 13:13:56  1982ad6f-0db0-5ae3-8090-1fe0b82d7e21        41   
35  16/11/2024 13:55:05  4e25cc7a-f744-5c18-b82d-7dd234072395        41   
36  16/11/2024 15:47:26  9e502950-aef7-568c-80d3-b3c6d62db398        55   
37  16/11/2024 16:42:12  f3d1fcbe-61f5-56c0-ab76-dce7d4f98e13        48   
38  16/11/2024 18:30:43  31603a5d-2550-5586-9d88-abb9ff7ccd76        43   
39  16/11/2024 18:37:09  24c588c8-7897-5fef-b675-8921af1aab92       NaN   
40  16/11/2024 18:53:28  26644736-c2d9-52c6-8e2b-c32fbcec3412        19   
41  16/11/2024 20:37:51  d754d3a7-5ebc-5c5d-bdac-2a84562603ff        36   
42  17/11/2024 00:03:23  fedb0c5f-d552-552b-8124-bfeee790c7c4        36   
43  17/11/2024 10:18:27  3d4443e4-6a96-584b-b941-39eebbd6f957        47   
44  17/11/2024 11:37:14  693b1e30-a43d-5498-821d-668a0d0925b2        45   
45  17/11/2024 14:24:30  3a08cfcd-5ef7-5350-922c-403904b3d1c0        55   
46  17/11/2024 17:02:37  040ce340-fde4-50f0-95d6-80a524b8adb7        59   
47  17/11/2024 19:21:17  fcc38cc1-b101-5ee5-9548-3554022421c7        33   
48  17/11/2024 22:40:50  6baadd18-584e-5f22-839b-2d811106210f        37   
49  17/11/2024 23:03:37  6bed0452-65a6-5d7b-a207-05b75e464ffc        60   
50  18/11/2024 13:16:10  fc2f505c-35e2-5978-96e3-a422b6eb1934  51 anos    
51  18/11/2024 13:17:51  72bda606-2554-5fe4-aac7-a9df524fb04e        31   
52  18/11/2024 13:18:08  40500e35-5efe-5b8a-ba

# Imputação de valores a dados faltantes

In [37]:
#substitui idade de sexo feminino pela mediana das idades
df.loc[50,2] = 51


In [39]:
df.groupby([3,2]).size().reset_index(name='Qauntidade')

3   2  Qauntidade
0                                            Feminino  19           1
1                                            Feminino  24           1
2                                            Feminino  33           1
3                                            Feminino  34           1
4                                            Feminino  36           1
5                                            Feminino  37           1
6                                            Feminino  39           1
7                                            Feminino  40           2
8                                            Feminino  41           1
9                                            Feminino  42           1
10                                           Feminino  43           1
11                                           Feminino  45           1
12                                           Feminino  47           1
13                                           Feminino  54           1
14                                           Feminino  60           1
15  Intersexo (popularmente conhecido como Hermafr...  47           1
16                                          Masculino  51           1
17                                          Masculino  25           1
18                                          Masculino  28           1
19                                          Masculino  30           1
20                                          Masculino  31           2
21                                          Masculino  33           5
22                                          Masculino  34           2
23                                          Masculino  36           4
24                                          Masculino  37           3
25                                          Masculino  40           2
26                                          Masculino  41           2
27                                          Masculino  42           1
28                                          Masculino  43           2
29                                          Masculino  44           2
30                                          Masculino  46           1
31                                          Masculino  47           1
32                                          Masculino  48           2
33                                          Masculino  51           1
34                                          Masculino  55           2
35                                          Masculino  59           3

In [41]:
df[2] = pd.to_numeric(df[2],errors='coerce')

In [43]:
df[df[3]=='Feminino'][2].mean()

39.625

In [45]:
df.loc[39,2] = 40 

In [47]:
valor_especifico = 'Youtube, TikTok, Whatsapp'

In [49]:
filtro = df[df[4] == valor_especifico]

In [51]:
filtro 

0                                     1     2         3   \
39  16/11/2024 18:37:09  24c588c8-7897-5fef-b675-8921af1aab92  40.0  Feminino   

                           4    5                                6    7    8   \
39  Youtube, TikTok, Whatsapp  NaN  Cisgênero (é o sexo que nasceu)  Sim  0.0   

     9   ...   41   42   43   44   45   46   47   48   49   50  
39  0.0  ...  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  

[1 rows x 51 columns]

In [53]:
df.mode()

0                                     1     2   \
0   16/11/2024 08:50:05  0135da91-4288-5475-8a7d-c06ac32e157d  33.0   
1   16/11/2024 08:56:56  020191c8-4c07-5bea-b769-f8f37cc30497   NaN   
2   16/11/2024 08:58:00  040ce340-fde4-50f0-95d6-80a524b8adb7   NaN   
3   16/11/2024 08:58:23  08d8653a-5fa3-55b5-a9cb-f658bbc46463   NaN   
4   16/11/2024 09:04:14  0934bf0f-83a2-5ce7-bdd6-8f6b596bb5ef   NaN   
5   16/11/2024 09:08:52  1982ad6f-0db0-5ae3-8090-1fe0b82d7e21   NaN   
6   16/11/2024 09:12:53  1c6101fe-3808-53d7-a804-c91dcc7e32d8   NaN   
7   16/11/2024 09:19:18  24c588c8-7897-5fef-b675-8921af1aab92   NaN   
8   16/11/2024 09:21:15  26644736-c2d9-52c6-8e2b-c32fbcec3412   NaN   
9   16/11/2024 09:25:20  28f1561e-9c1b-5fae-a52d-1173b3285da2   NaN   
10  16/11/2024 09:28:39  2903def3-aa2f-5bf3-8d43-f9396e259be8   NaN   
11  16/11/2024 09:44:19  2c35c15d-09d5-51ff-b647-2dbc1bc31b32   NaN   
12  16/11/2024 09:57:47  3138d431-cc7b-59f3-bdcf-10cd82c55545   NaN   
13  16/11/2024 09:58:19  31603a5d-2550-5586-9d88-abb9ff7ccd76   NaN   
14  16/11/2024 10:35:56  39c3fb67-2006-5cfc-8c6e-92b9638e01c3   NaN   
15  16/11/2024 10:43:45  3a08cfcd-5ef7-5350-922c-403904b3d1c0   NaN   
16  16/11/2024 10:44:43  3d4443e4-6a96-584b-b941-39eebbd6f957   NaN   
17  16/11/2024 10:49:57  3f123bb8-6b37-58e8-bccd-035231c8a49c   NaN   
18  16/11/2024 10:58:30  40500e35-5efe-5b8a-ba4f-a541d1f24af0   NaN   
19  16/11/2024 10:59:04  4935d0e4-ed00-523c-8d16-9dcc2273d6c3   NaN   
20  16/11/2024 11:28:07  4e25cc7a-f744-5c18-b82d-7dd234072395   NaN   
21  16/11/2024 11:28:45  4fe3cb6d-8d9f-5fdd-87fa-13481495a0c4   NaN   
22  16/11/2024 11:42:43  52101e6a-ca49-5844-a546-155aa08bf771   NaN   
23  16/11/2024 11:42:45  5553edd9-4ffa-5f9e-b23c-0ec586faac92   NaN   
24  16/11/2024 11:52:04  5a94a0af-1f02-518c-9d97-4d84c2b4a238   NaN   
25  16/11/2024 11:56:56  6180a5a7-24b2-578d-a9c8-6fe019950127   NaN   
26  16/11/2024 12:02:21  66e637f0-f501-5faa-bd9d-3c32504b27f2   NaN   
27  16/11/2024 12:06:47  67f34955-eeb7-5c32-98e7-a97e76319123   NaN   
28  16/11/2024 12:17:28  693b1e30-a43d-5498-821d-668a0d0925b2   NaN   
29  16/11/2024 12:20:31  6baadd18-584e-5f22-839b-2d811106210f   NaN   
30  16/11/2024 12:29:09  6bed0452-65a6-5d7b-a207-05b75e464ffc   NaN   
31  16/11/2024 12:32:33  72bda606-2554-5fe4-aac7-a9df524fb04e   NaN   
32  16/11/2024 12:48:11  76f728ad-95de-5906-81cf-682fcbf25c03   NaN   
33  16/11/2024 12:54:04  7d3aed80-5b84-551e-88a5-e78768c61784   NaN   
34  16/11/2024 13:13:56  7e960c6a-1666-530f-8352-b2b57322a37b   NaN   
35  16/11/2024 13:55:05  844ab66e-8e20-57df-92c1-2ecb27388676   NaN   
36  16/11/2024 15:47:26  89af1ea9-ed96-5a12-ac1f-569141e4dd3b   NaN   
37  16/11/2024 16:42:12  8f30b1fa-511d-5044-948d-268c86cb55df   NaN   
38  16/11/2024 18:30:43  92f6a363-67a4-5b0b-a2c8-83fdec015808   NaN   
39  16/11/2024 18:37:09  9e19ad96-acaf-5f4c-8d6f-68fd689b4a28   NaN   
40  16/11/2024 18:53:28  9e502950-aef7-568c-80d3-b3c6d62db398   NaN   
41  16/11/2024 20:37:51  b6c4ce6b-fa2c-58b1-902f-5a35821091ab   NaN   
42  17/11/2024 00:03:23  bbb15780-cc69-5b92-9733-a5b7ac49cf84   NaN   
43  17/11/2024 10:18:27  cecd8d29-012e-5dbf-aad7-61887822eba5   NaN   
44  17/11/2024 11:37:14  d4b48127-c1df-5ef8-93a1-e7aa4250a15a   NaN   
45  17/11/2024 14:24:30  d5b52350-81cf-50a5-b462-85c05c01ebec   NaN   
46  17/11/2024 17:02:37  d6619a23-2eb7-5c97-8f3a-5d1ed07daadb   NaN   
47  17/11/2024 19:21:17  d754d3a7-5ebc-5c5d-bdac-2a84562603ff   NaN   
48  17/11/2024 22:40:50  da896799-9ea2-5e91-ad37-3a9bf6a5eea9   NaN   
49  17/11/2024 23:03:37  e96fb289-e520-57c8-8b68-880765086fee   NaN   
50  18/11/2024 13:16:10  ee378c51-702f-5e5f-90d7-8929e279a999   NaN   
51  18/11/2024 13:17:51  ef094ef4-c311-52ab-994b-a5e2943c8c04   NaN   
52  18/11/2024 13:18:08  efd75239-cc3e-59c0-97e1-400a60b59516   NaN   
53  18/11/2024 13:30:14  f3d1fcbe-61f5-56c0-ab76-dce7d4f98e13   NaN   
54  18/11/2024 15:01:24  fc2f505c-35e2-5978-96e3-a422b6eb1934   NaN   
55  18/11/2024 18:46:50  fcc38cc1-b101-5ee5-9

In [55]:
def substituiMediana(ds,coluna):
    mediana = df[coluna].median()
    ds[coluna].fillna(mediana, inplace=True)
    
def substituiModa(ds,coluna):
    moda = df[coluna].mode()
    ds[coluna].fillna(moda, inplace=True)

In [57]:
df[6] = df[6].fillna('Cisgênero (é o sexo que nasceu)')

In [59]:
df

0                                     1     2   \
0   16/11/2024 08:50:05  2903def3-aa2f-5bf3-8d43-f9396e259be8  41.0   
1   16/11/2024 08:56:56  52101e6a-ca49-5844-a546-155aa08bf771  33.0   
2   16/11/2024 08:58:00  0135da91-4288-5475-8a7d-c06ac32e157d  51.0   
3   16/11/2024 08:58:23  ef094ef4-c311-52ab-994b-a5e2943c8c04  37.0   
4   16/11/2024 09:04:14  4fe3cb6d-8d9f-5fdd-87fa-13481495a0c4  30.0   
5   16/11/2024 09:08:52  8f30b1fa-511d-5044-948d-268c86cb55df  36.0   
6   16/11/2024 09:12:53  844ab66e-8e20-57df-92c1-2ecb27388676  37.0   
7   16/11/2024 09:19:18  da896799-9ea2-5e91-ad37-3a9bf6a5eea9  34.0   
8   16/11/2024 09:21:15  76f728ad-95de-5906-81cf-682fcbf25c03  33.0   
9   16/11/2024 09:25:20  3f123bb8-6b37-58e8-bccd-035231c8a49c  44.0   
10  16/11/2024 09:28:39  39c3fb67-2006-5cfc-8c6e-92b9638e01c3  40.0   
11  16/11/2024 09:44:19  bbb15780-cc69-5b92-9733-a5b7ac49cf84  43.0   
12  16/11/2024 09:57:47  5a94a0af-1f02-518c-9d97-4d84c2b4a238  59.0   
13  16/11/2024 09:58:19  9e19ad96-acaf-5f4c-8d6f-68fd689b4a28  34.0   
14  16/11/2024 10:35:56  7e960c6a-1666-530f-8352-b2b57322a37b  37.0   
15  16/11/2024 10:43:45  89af1ea9-ed96-5a12-ac1f-569141e4dd3b  33.0   
16  16/11/2024 10:44:43  5553edd9-4ffa-5f9e-b23c-0ec586faac92  33.0   
17  16/11/2024 10:49:57  d6619a23-2eb7-5c97-8f3a-5d1ed07daadb  40.0   
18  16/11/2024 10:58:30  ee378c51-702f-5e5f-90d7-8929e279a999  33.0   
19  16/11/2024 10:59:04  6180a5a7-24b2-578d-a9c8-6fe019950127  36.0   
20  16/11/2024 11:28:07  b6c4ce6b-fa2c-58b1-902f-5a35821091ab  34.0   
21  16/11/2024 11:28:45  2c35c15d-09d5-51ff-b647-2dbc1bc31b32  54.0   
22  16/11/2024 11:42:43  7d3aed80-5b84-551e-88a5-e78768c61784  43.0   
23  16/11/2024 11:42:45  4935d0e4-ed00-523c-8d16-9dcc2273d6c3  47.0   
24  16/11/2024 11:52:04  66e637f0-f501-5faa-bd9d-3c32504b27f2  28.0   
25  16/11/2024 11:56:56  cecd8d29-012e-5dbf-aad7-61887822eba5  24.0   
26  16/11/2024 12:02:21  92f6a363-67a4-5b0b-a2c8-83fdec015808  40.0   
27  16/11/2024 12:06:47  efd75239-cc3e-59c0-97e1-400a60b59516  46.0   
28  16/11/2024 12:17:28  28f1561e-9c1b-5fae-a52d-1173b3285da2  48.0   
29  16/11/2024 12:20:31  d4b48127-c1df-5ef8-93a1-e7aa4250a15a  59.0   
30  16/11/2024 12:29:09  d5b52350-81cf-50a5-b462-85c05c01ebec  25.0   
31  16/11/2024 12:32:33  3138d431-cc7b-59f3-bdcf-10cd82c55545  36.0   
32  16/11/2024 12:48:11  1c6101fe-3808-53d7-a804-c91dcc7e32d8  40.0   
33  16/11/2024 12:54:04  08d8653a-5fa3-55b5-a9cb-f658bbc46463  42.0   
34  16/11/2024 13:13:56  1982ad6f-0db0-5ae3-8090-1fe0b82d7e21  41.0   
35  16/11/2024 13:55:05  4e25cc7a-f744-5c18-b82d-7dd234072395  41.0   
36  16/11/2024 15:47:26  9e502950-aef7-568c-80d3-b3c6d62db398  55.0   
37  16/11/2024 16:42:12  f3d1fcbe-61f5-56c0-ab76-dce7d4f98e13  48.0   
38  16/11/2024 18:30:43  31603a5d-2550-5586-9d88-abb9ff7ccd76  43.0   
39  16/11/2024 18:37:09  24c588c8-7897-5fef-b675-8921af1aab92  40.0   
40  16/11/2024 18:53:28  26644736-c2d9-52c6-8e2b-c32fbcec3412  19.0   
41  16/11/2024 20:37:51  d754d3a7-5ebc-5c5d-bdac-2a84562603ff  36.0   
42  17/11/2024 00:03:23  fedb0c5f-d552-552b-8124-bfeee790c7c4  36.0   
43  17/11/2024 10:18:27  3d4443e4-6a96-584b-b941-39eebbd6f957  47.0   
44  17/11/2024 11:37:14  693b1e30-a43d-5498-821d-668a0d0925b2  45.0   
45  17/11/2024 14:24:30  3a08cfcd-5ef7-5350-922c-403904b3d1c0  55.0   
46  17/11/2024 17:02:37  040ce340-fde4-50f0-95d6-80a524b8adb7  59.0   
47  17/11/2024 19:21:17  fcc38cc1-b101-5ee5-9548-3554022421c7  33.0   
48  17/11/2024 22:40:50  6baadd18-584e-5f22-839b-2d811106210f  37.0   
49  17/11/2024 23:03:37  6bed0452-65a6-5d7b-a207-05b75e464ffc  60.0   
50  18/11/2024 13:16:10  fc2f505c-35e2-5978-96e3-a422b6eb1934  51.0   
51  18/11/2024 13:17:51  72bda606-2554-5fe4-aac7-a9df524fb04e  31.0   
52  18/11/2024 13:18:08  40500e35-5efe-5b8a-ba4f-a541d1f24af0  47.0   
53  18/11/2024 13:30:14  0934bf0f-83a2-5ce7-bdd6-8f6b596bb5ef  44.0   
54  18/11/2024 15:01:24  e96fb289-e520-57c8-8b68-880765086fee  39.0   
55  18/11/2024 18:46:50  020191c8-4c07-5bea-b

In [61]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 51 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   0       57 non-null     object 
 1   1       57 non-null     object 
 2   2       57 non-null     float64
 3   3       57 non-null     object 
 4   4       57 non-null     object 
 5   5       55 non-null     object 
 6   6       57 non-null     object 
 7   7       57 non-null     object 
 8   8       57 non-null     float64
 9   9       57 non-null     float64
 10  10      57 non-null     float64
 11  11      57 non-null     float64
 12  12      57 non-null     float64
 13  13      57 non-null     float64
 14  14      57 non-null     float64
 15  15      57 non-null     float64
 16  16      57 non-null     float64
 17  17      57 non-null     float64
 18  18      57 non-null     float64
 19  19      55 non-null     object 
 20  20      56 non-null     object 
 21  21      52 non-null     object 
 22  22  

In [63]:
representacao 

{'Carimbo de data/hora': 0,
 'Endereço de e-mail': 1,
 'Qual é a sua idade?': 2,
 'Gênero': 3,
 'Quais plataformas de mídia social você costuma usar?': 4,
 'Cidade onde Mora': 5,
 'Sexo': 6,
 'Está empregado': 7,
 'Já foi diagnosticado por um profissional com algum dos itens: [Nenhum]': 8,
 'Já foi diagnosticado por um profissional com algum dos itens: [Depressão]': 9,
 'Já foi diagnosticado por um profissional com algum dos itens: [Ansiedade]': 10,
 'Já foi diagnosticado por um profissional com algum dos itens: [Estresse]': 11,
 'Já foi diagnosticado por um profissional com algum dos itens: [TDAH]': 12,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno Bipolar]': 13,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno de ansiedade social :]': 14,
 'Já foi diagnosticado por um profissional com algum dos itens: [Fobia de Perda de Conexão ( Ansiedade relacionada à ausência de acesso ao celular ou redes sociais, causando angústia e desconf

In [65]:
colunas = list(range(8,19))

In [67]:
colunas.insert(0,0)
colunas

[0, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18]

In [69]:
dsAnterior = df[colunas]
dsAnterior

0    8    9    10   11   12   13   14   15   16   17   18
0   16/11/2024 08:50:05  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
1   16/11/2024 08:56:56  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
2   16/11/2024 08:58:00  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
3   16/11/2024 08:58:23  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
4   16/11/2024 09:04:14  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
5   16/11/2024 09:08:52  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
6   16/11/2024 09:12:53  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
7   16/11/2024 09:19:18  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
8   16/11/2024 09:21:15  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
9   16/11/2024 09:25:20  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
10  16/11/2024 09:28:39  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
11  16/11/2024 09:44:19  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
12  16/11/2024 09:57:47  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
13  16/11/2024 09:58:19  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
14  16/11/2024 10:35:56  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0
15  16/11/2024 10:43:45  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0
16  16/11/2024 10:44:43  0.0  1.0  1.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0
17  16/11/2024 10:49:57  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
18  16/11/2024 10:58:30  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
19  16/11/2024 10:59:04  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
20  16/11/2024 11:28:07  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
21  16/11/2024 11:28:45  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
22  16/11/2024 11:42:43  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
23  16/11/2024 11:42:45  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
24  16/11/2024 11:52:04  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
25  16/11/2024 11:56:56  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.0
26  16/11/2024 12:02:21  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
27  16/11/2024 12:06:47  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
28  16/11/2024 12:17:28  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
29  16/11/2024 12:20:31  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
30  16/11/2024 12:29:09  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
31  16/11/2024 12:32:33  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
32  16/11/2024 12:48:11  0.0  1.0  1.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0
33  16/11/2024 12:54:04  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
34  16/11/2024 13:13:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
35  16/11/2024 13:55:05  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
36  16/11/2024 15:47:26  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
37  16/11/2024 16:42:12  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
38  16/11/2024 18:30:43  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
39  16/11/2024 18:37:09  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
40  16/11/2024 18:53:28  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
41  16/11/2024 20:37:51  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
42  17/11/2024 00:03:23  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
43  17/11/2024 10:18:27  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
44  17/11/2024 11:37:14  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
45  17/11/2024 14:24:30  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
46  17/11/2024 17:02:37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
47  17/11/2024 19:21:17  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
48  17/11/2024 22:40:50  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
49  17/11/2024 23:03:37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0

In [71]:
colunas = list(range(40,51))

In [73]:
colunas.insert(0,0)
colunas

[0, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50]

In [75]:
dsPosterior = df[colunas]
dsPosterior

0    40   41   42   43   44   45   46   47   48   49   50
0   16/11/2024 08:50:05  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
1   16/11/2024 08:56:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
2   16/11/2024 08:58:00  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
3   16/11/2024 08:58:23  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
4   16/11/2024 09:04:14  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
5   16/11/2024 09:08:52  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
6   16/11/2024 09:12:53  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
7   16/11/2024 09:19:18  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
8   16/11/2024 09:21:15  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
9   16/11/2024 09:25:20  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
10  16/11/2024 09:28:39  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
11  16/11/2024 09:44:19  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
12  16/11/2024 09:57:47  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
13  16/11/2024 09:58:19  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
14  16/11/2024 10:35:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
15  16/11/2024 10:43:45  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
16  16/11/2024 10:44:43  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
17  16/11/2024 10:49:57  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
18  16/11/2024 10:58:30  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
19  16/11/2024 10:59:04  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
20  16/11/2024 11:28:07  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
21  16/11/2024 11:28:45  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
22  16/11/2024 11:42:43  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
23  16/11/2024 11:42:45  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
24  16/11/2024 11:52:04  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
25  16/11/2024 11:56:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
26  16/11/2024 12:02:21  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
27  16/11/2024 12:06:47  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
28  16/11/2024 12:17:28  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
29  16/11/2024 12:20:31  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
30  16/11/2024 12:29:09  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
31  16/11/2024 12:32:33  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
32  16/11/2024 12:48:11  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
33  16/11/2024 12:54:04  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
34  16/11/2024 13:13:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
35  16/11/2024 13:55:05  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
36  16/11/2024 15:47:26  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
37  16/11/2024 16:42:12  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
38  16/11/2024 18:30:43  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
39  16/11/2024 18:37:09  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
40  16/11/2024 18:53:28  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
41  16/11/2024 20:37:51  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
42  17/11/2024 00:03:23  1.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
43  17/11/2024 10:18:27  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
44  17/11/2024 11:37:14  1.0  1.0  1.0  0.0  0.0  1.0  0.0  1.0  0.0  1.0  0.0
45  17/11/2024 14:24:30  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
46  17/11/2024 17:02:37  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
47  17/11/2024 19:21:17  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
48  17/11/2024 22:40:50  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0
49  17/11/2024 23:03:37  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  1.0  0

In [77]:
dfCensurado = pd.merge(dsAnterior,dsPosterior, on=0, how='inner')
dfCensurado

0    8    9    10   11   12   13   14   15   16  ...  \
0   16/11/2024 08:50:05  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
1   16/11/2024 08:56:56  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
2   16/11/2024 08:58:00  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  ...   
3   16/11/2024 08:58:23  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  ...   
4   16/11/2024 09:04:14  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
5   16/11/2024 09:08:52  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
6   16/11/2024 09:12:53  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
7   16/11/2024 09:19:18  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
8   16/11/2024 09:21:15  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
9   16/11/2024 09:25:20  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
10  16/11/2024 09:28:39  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
11  16/11/2024 09:44:19  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
12  16/11/2024 09:57:47  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
13  16/11/2024 09:58:19  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
14  16/11/2024 10:35:56  0.0  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  ...   
15  16/11/2024 10:43:45  0.0  1.0  1.0  1.0  1.0  0.0  0.0  0.0  0.0  ...   
16  16/11/2024 10:44:43  0.0  1.0  1.0  0.0  0.0  0.0  1.0  0.0  0.0  ...   
17  16/11/2024 10:49:57  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
18  16/11/2024 10:58:30  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
19  16/11/2024 10:59:04  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
20  16/11/2024 11:28:07  0.0  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  ...   
21  16/11/2024 11:28:45  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
22  16/11/2024 11:42:43  0.0  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
23  16/11/2024 11:42:45  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
24  16/11/2024 11:52:04  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
25  16/11/2024 11:56:56  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  1.0  ...   
26  16/11/2024 12:02:21  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
27  16/11/2024 12:06:47  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
28  16/11/2024 12:17:28  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
29  16/11/2024 12:20:31  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
30  16/11/2024 12:29:09  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...   
31  16/11/2024 12:32:33  0.0  0.0  1.0  1.0  0.0  0.0  0.0  0.0  0.0  ...   
32  16/11/2024 12:48:11  0.0  1.0  1.0  0.0  0.0  1.0  0.0  0.0  0.0  ...   
33  16/11/2024 12:54:04  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
34  16/11/2024 13:13:56  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
35  16/11/2024 13:55:05  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
36  16/11/2024 15:47:26  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
37  16/11/2024 16:42:12  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
38  16/11/2024 18:30:43  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
39  16/11/2024 18:37:09  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
40  16/11/2024 18:53:28  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
41  16/11/2024 20:37:51  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
42  17/11/2024 00:03:23  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
43  17/11/2024 10:18:27  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
44  17/11/2024 11:37:14  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
45  17/11/2024 14:24:30  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
46  17/11/2024 17:02:37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
47  17/11/2024 19:21:17  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
48  17/11/2024 22:40:50  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
49  17/11/2024 23:03:37  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
50  18/11/2024 13:16:10  1.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  ...   
51  18/11/2024 13

In [79]:
# Converter apenas as colunas com tipo float para bool
for col in dfCensurado.select_dtypes(include=['float']).columns:
    dfCensurado[col] = dfCensurado[col].astype(bool)

for col in dsAnterior.select_dtypes(include=['float']).columns:
    dsAnterior[col] = dsAnterior[col].astype(bool)

for col in dsPosterior.select_dtypes(include=['float']).columns:
    dsPosterior[col] = dsPosterior[col].astype(bool)

/tmp/ipykernel_6332/461485226.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dsAnterior[col] = dsAnterior[col].astype(bool)
/tmp/ipykernel_6332/461485226.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dsAnterior[col] = dsAnterior[col].astype(bool)
/tmp/ipykernel_6332/461485226.py:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/panda

In [81]:
dfCensurado[50]

0     False
1     False
2     False
3     False
4     False
5     False
6     False
7     False
8     False
9     False
10    False
11    False
12    False
13    False
14    False
15    False
16    False
17    False
18    False
19    False
20    False
21    False
22    False
23    False
24    False
25    False
26    False
27    False
28    False
29    False
30    False
31    False
32    False
33    False
34    False
35    False
36    False
37    False
38    False
39    False
40    False
41    False
42    False
43    False
44    False
45    False
46    False
47    False
48    False
49    False
50    False
51    False
52    False
53    False
54    False
55    False
56    False
Name: 50, dtype: bool

In [83]:
dfCensurado

0      8      9      10     11     12     13     14  \
0   16/11/2024 08:50:05   True  False  False  False  False  False  False   
1   16/11/2024 08:56:56   True  False  False  False  False  False  False   
2   16/11/2024 08:58:00  False  False  False   True  False  False  False   
3   16/11/2024 08:58:23  False  False  False   True  False  False  False   
4   16/11/2024 09:04:14   True  False  False  False  False  False  False   
5   16/11/2024 09:08:52  False  False  False  False  False  False  False   
6   16/11/2024 09:12:53  False  False   True  False  False  False  False   
7   16/11/2024 09:19:18   True  False  False  False  False  False  False   
8   16/11/2024 09:21:15   True  False  False  False  False  False  False   
9   16/11/2024 09:25:20   True  False  False  False  False  False  False   
10  16/11/2024 09:28:39   True  False  False  False  False  False  False   
11  16/11/2024 09:44:19   True  False  False  False  False  False  False   
12  16/11/2024 09:57:47  False  False   True  False  False  False  False   
13  16/11/2024 09:58:19   True  False  False  False  False  False  False   
14  16/11/2024 10:35:56  False  False  False  False   True  False  False   
15  16/11/2024 10:43:45  False   True   True   True   True  False  False   
16  16/11/2024 10:44:43  False   True   True  False  False  False   True   
17  16/11/2024 10:49:57   True  False  False  False  False  False  False   
18  16/11/2024 10:58:30  False  False   True  False  False  False  False   
19  16/11/2024 10:59:04  False  False   True  False  False  False  False   
20  16/11/2024 11:28:07  False  False  False   True  False  False  False   
21  16/11/2024 11:28:45   True  False  False  False  False  False  False   
22  16/11/2024 11:42:43  False  False   True  False  False  False  False   
23  16/11/2024 11:42:45   True  False  False  False  False  False  False   
24  16/11/2024 11:52:04  False   True  False  False  False  False  False   
25  16/11/2024 11:56:56  False   True   True  False  False  False  False   
26  16/11/2024 12:02:21   True  False  False  False  False  False  False   
27  16/11/2024 12:06:47   True  False  False  False  False  False  False   
28  16/11/2024 12:17:28   True  False  False  False  False  False  False   
29  16/11/2024 12:20:31   True  False  False  False  False  False  False   
30  16/11/2024 12:29:09  False  False   True   True  False  False  False   
31  16/11/2024 12:32:33  False  False   True   True  False  False  False   
32  16/11/2024 12:48:11  False   True   True  False  False   True  False   
33  16/11/2024 12:54:04  False  False  False  False  False  False  False   
34  16/11/2024 13:13:56  False  False  False  False  False  False  False   
35  16/11/2024 13:55:05  False  False  False  False  False  False  False   
36  16/11/2024 15:47:26   True  False  False  False  False  False  False   
37  16/11/2024 16:42:12   True  False  False  False  False  False  False   
38  16/11/2024 18:30:43   True  False  False  False  False  False  False   
39  16/11/2024 18:37:09  False  False  False  False  False  False  False   
40  16/11/2024 18:53:28  False  False  False  False  False  False  False   
41  16/11/2024 20:37:51   True  False  False  False  False  False  False   
42  17/11/2024 00:03:23  False  False  False  False  False  False  False   
43  17/11/2024 10:18:27   True  False  False  False  False  False  False   
44  17/11/2024 11:37:14  False  False  False  False  False  False  False   
45  17/11/2024 14:24:30  False  False  False  False  False  False  False   
46  17/11/2024 17:02:37  False  False  False  False  False  False  False   
47  17/11/2024 19:21:17   True  False  False  False  False  False  False   
48  17/11/2024 22:40:50   True  False  False  False  False  False  False   
49  17/11/2024 23:03:37  False  False  False  False  False  False  False   
50  18/11/2024 13:16:10   True  False  False  False  False  False  False   
51  18/11/2024 13:17:51   True  False  False  False  False  False  Fa

In [94]:
 dfCensurado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 23 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   0       57 non-null     object
 1   8       57 non-null     bool  
 2   9       57 non-null     bool  
 3   10      57 non-null     bool  
 4   11      57 non-null     bool  
 5   12      57 non-null     bool  
 6   13      57 non-null     bool  
 7   14      57 non-null     bool  
 8   15      57 non-null     bool  
 9   16      57 non-null     bool  
 10  17      57 non-null     bool  
 11  18      57 non-null     bool  
 12  40      57 non-null     bool  
 13  41      57 non-null     bool  
 14  42      57 non-null     bool  
 15  43      57 non-null     bool  
 16  44      57 non-null     bool  
 17  45      57 non-null     bool  
 18  46      57 non-null     bool  
 19  47      57 non-null     bool  
 20  48      57 non-null     bool  
 21  49      57 non-null     bool  
 22  50      57 non-null     bool

In [155]:
dfCensurado_novo = pd.DataFrame()

In [151]:
dsAnterior[8]

0      True
1      True
2     False
3     False
4      True
5     False
6     False
7      True
8      True
9      True
10     True
11     True
12    False
13     True
14    False
15    False
16    False
17     True
18    False
19    False
20    False
21     True
22    False
23     True
24    False
25    False
26     True
27     True
28     True
29     True
30    False
31    False
32    False
33    False
34    False
35    False
36     True
37     True
38     True
39    False
40    False
41     True
42    False
43     True
44    False
45    False
46    False
47     True
48     True
49    False
50     True
51     True
52    False
53     True
54     True
55    False
56     True
Name: 8, dtype: bool

In [159]:

# for col1, col2 in zip(dsAnterior.drop(0,axis=1), dsPosterior.drop(0,axis=1)):
#     print(col1, col2)
#     dfCensurado_novo[f'Fusao_{col1}_{col2}'] = dsAnterior[col1] | dsPosterior[col2]
dfCensurado_novo[f'Fusao_{8}_{50}'] = dsAnterior[8] | dsPosterior[50]
dfCensurado_novo[f'Fusao_{9}_{40}'] = dsAnterior[9] | dsPosterior[40]
dfCensurado_novo[f'Fusao_{10}_{41}'] = dsAnterior[10] | dsPosterior[41]
dfCensurado_novo[f'Fusao_{11}_{42}'] = dsAnterior[11] | dsPosterior[42]
dfCensurado_novo[f'Fusao_{12}_{43}'] = dsAnterior[12] | dsPosterior[43]
dfCensurado_novo[f'Fusao_{13}_{44}'] = dsAnterior[13] | dsPosterior[44]
dfCensurado_novo[f'Fusao_{14}_{45}'] = dsAnterior[14] | dsPosterior[45]
dfCensurado_novo[f'Fusao_{15}_{46}'] = dsAnterior[15] | dsPosterior[46]
dfCensurado_novo[f'Fusao_{16}_{47}'] = dsAnterior[16] | dsPosterior[47]
dfCensurado_novo[f'Fusao_{17}_{48}'] = dsAnterior[17] | dsPosterior[48]
dfCensurado_novo[f'Fusao_{18}_{49}'] = dsAnterior[18] | dsPosterior[49]
dfCensurado_novo

Fusao_8_50  Fusao_9_40  Fusao_10_41  Fusao_11_42  Fusao_12_43  \
0         True       False        False        False        False   
1         True       False        False        False        False   
2        False       False        False         True        False   
3        False       False        False         True        False   
4         True       False        False        False        False   
5        False       False        False        False        False   
6        False       False         True        False        False   
7         True       False        False        False        False   
8         True       False        False        False        False   
9         True       False        False        False        False   
10        True       False        False        False        False   
11        True       False        False        False        False   
12       False       False         True        False        False   
13        True       False        False        False        False   
14       False       False        False        False         True   
15       False        True         True         True         True   
16       False        True         True        False        False   
17        True       False        False        False        False   
18       False       False         True        False        False   
19       False       False         True        False        False   
20       False       False        False         True        False   
21        True       False        False        False        False   
22       False       False         True        False        False   
23        True       False        False        False        False   
24       False        True        False        False        False   
25       False        True         True        False        False   
26        True       False        False        False        False   
27        True       False        False        False        False   
28        True       False        False        False        False   
29        True       False        False        False        False   
30       False       False         True         True        False   
31       False       False         True         True        False   
32       False        True         True        False        False   
33       False       False        False        False        False   
34       False       False        False        False        False   
35       False       False        False         True         True   
36        True       False        False        False        False   
37        True       False        False        False        False   
38        True       False        False        False        False   
39       False        True         True        False        False   
40       False        True        False        False        False   
41        True       False        False        False        False   
42       False        True         True        False        False   
43        True       False        False        False        False   
44       False        True         True         True        False   
45       False        True        False        False        False   
46       False       False         True        False        False   
47        True       False        False        False        False   
48        True       False        False        False        False   
49       False       False         True         True        False   
50        True       False        False        False        False   
51        True       False        False        False        False   
52       False        True         True        False         True   
53        True       False        False        False        False   
54        True       False        False        False        False   
55       False        True         True        False         True   
56        True       False        False        False        False   

 

In [161]:
dfCensurado_novo.describe()

Fusao_8_50 Fusao_9_40 Fusao_10_41 Fusao_11_42 Fusao_12_43 Fusao_13_44  \
count          57         57          57          57          57          57   
unique          2          2           2           2           2           2   
top         False      False       False       False       False       False   
freq           29         45          39          48          52          56   

       Fusao_14_45 Fusao_15_46 Fusao_16_47 Fusao_17_48 Fusao_18_49  
count           57          57          57          57          57  
unique           2           1           2           2           2  
top          False       False       False       False       False  
freq            55          57          55          56          56

In [163]:
dfCensurado_novo.sum()

Fusao_8_50     28
Fusao_9_40     12
Fusao_10_41    18
Fusao_11_42     9
Fusao_12_43     5
Fusao_13_44     1
Fusao_14_45     2
Fusao_15_46     0
Fusao_16_47     2
Fusao_17_48     1
Fusao_18_49     1
dtype: int64

In [139]:
representacao 

{'Carimbo de data/hora': 0,
 'Endereço de e-mail': 1,
 'Qual é a sua idade?': 2,
 'Gênero': 3,
 'Quais plataformas de mídia social você costuma usar?': 4,
 'Cidade onde Mora': 5,
 'Sexo': 6,
 'Está empregado': 7,
 'Já foi diagnosticado por um profissional com algum dos itens: [Nenhum]': 8,
 'Já foi diagnosticado por um profissional com algum dos itens: [Depressão]': 9,
 'Já foi diagnosticado por um profissional com algum dos itens: [Ansiedade]': 10,
 'Já foi diagnosticado por um profissional com algum dos itens: [Estresse]': 11,
 'Já foi diagnosticado por um profissional com algum dos itens: [TDAH]': 12,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno Bipolar]': 13,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno de ansiedade social :]': 14,
 'Já foi diagnosticado por um profissional com algum dos itens: [Fobia de Perda de Conexão ( Ansiedade relacionada à ausência de acesso ao celular ou redes sociais, causando angústia e desconf

In [181]:
df_deduplicado = pd.concat([df[list(range(0,8))],df[list(range(19,40))],dfCensurado_novo],axis=1)
df_deduplicado.head()

0                                     1     2          3  \
0  16/11/2024 08:50:05  2903def3-aa2f-5bf3-8d43-f9396e259be8  41.0  Masculino   
1  16/11/2024 08:56:56  52101e6a-ca49-5844-a546-155aa08bf771  33.0  Masculino   
2  16/11/2024 08:58:00  0135da91-4288-5475-8a7d-c06ac32e157d  51.0  Masculino   
3  16/11/2024 08:58:23  ef094ef4-c311-52ab-994b-a5e2943c8c04  37.0  Masculino   
4  16/11/2024 09:04:14  4fe3cb6d-8d9f-5fdd-87fa-13481495a0c4  30.0  Masculino   

                                                   4                5  \
0                                 Linkedin, Whatsapp          Niterói   
1  Instagram, Facebook, Youtube, Linkedin, TikTok...      São Gonçalo   
2                                           Whatsapp         Niterói    
3   Instagram, Facebook, Youtube, Linkedin, Whatsapp  Rio de Janeiro    
4         Instagram, Facebook, Twitter (X), Whatsapp     São Gonçalo    

                                 6    7               19   20  ... Fusao_9_40  \
0  Cisgênero (é o sexo que nasceu)  Sim  Superior 30 mil  Sim  ...      False   
1  Cisgênero (é o sexo que nasceu)  Sim       Atè 10 mil  Sim  ...      False   
2  Cisgênero (é o sexo que nasceu)  Sim       Atè 10 mil  Sim  ...      False   
3  Cisgênero (é o sexo que nasceu)  Sim       Atè 10 mil  Sim  ...      False   
4  Cisgênero (é o sexo que nasceu)  Sim        Até 5 mil  Sim  ...      False   

   Fusao_10_41  Fusao_11_42  Fusao_12_43 Fusao_13_44  Fusao_14_45  \
0        False        False        False       False        False   
1        False        False        False       False        False   
2        False         True        False       False        False   
3        False         True        False       False        False   
4        False        False        False       False        False   

   Fusao_15_46  Fusao_16_47  Fusao_17_48  Fusao_18_49  
0        False        False        False        False  
1        False        False        False        False  
2        False        False        False        False  
3        False        False        False        False  
4        False        False        False        False  

[5 rows x 40 columns]

In [183]:
df_deduplicado.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 57 entries, 0 to 56
Data columns (total 40 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   0            57 non-null     object 
 1   1            57 non-null     object 
 2   2            57 non-null     float64
 3   3            57 non-null     object 
 4   4            57 non-null     object 
 5   5            55 non-null     object 
 6   6            57 non-null     object 
 7   7            57 non-null     object 
 8   19           55 non-null     object 
 9   20           56 non-null     object 
 10  21           52 non-null     object 
 11  22           56 non-null     float64
 12  23           56 non-null     float64
 13  24           57 non-null     int64  
 14  25           57 non-null     object 
 15  26           57 non-null     int64  
 16  27           56 non-null     float64
 17  28           56 non-null     float64
 18  29           55 non-null     float64
 19  30        

In [185]:
# df_deduplicado.to_csv('datasetPesquisaTratado.csv')

# EDA e perfilação

In [205]:
representacao

{'Carimbo de data/hora': 0,
 'Endereço de e-mail': 1,
 'Qual é a sua idade?': 2,
 'Gênero': 3,
 'Quais plataformas de mídia social você costuma usar?': 4,
 'Cidade onde Mora': 5,
 'Sexo': 6,
 'Está empregado': 7,
 'Já foi diagnosticado por um profissional com algum dos itens: [Nenhum]': 8,
 'Já foi diagnosticado por um profissional com algum dos itens: [Depressão]': 9,
 'Já foi diagnosticado por um profissional com algum dos itens: [Ansiedade]': 10,
 'Já foi diagnosticado por um profissional com algum dos itens: [Estresse]': 11,
 'Já foi diagnosticado por um profissional com algum dos itens: [TDAH]': 12,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno Bipolar]': 13,
 'Já foi diagnosticado por um profissional com algum dos itens: [Transtorno de ansiedade social :]': 14,
 'Já foi diagnosticado por um profissional com algum dos itens: [Fobia de Perda de Conexão ( Ansiedade relacionada à ausência de acesso ao celular ou redes sociais, causando angústia e desconf

In [213]:
len(df_deduplicado.keys()),df_deduplicado.keys(),len(representacao.keys())

(40,
 Index(['0', '1', '2', '3', '4', '5', '6', '7', '19', '20', '21', '22', '23',
        '24', '25', '26', '27', '28', '29', '30', '31', '32', '33', '34', '35',
        '36', '37', '38', '39', 'Fusao_8_50', 'Fusao_9_40', 'Fusao_10_41',
        'Fusao_11_42', 'Fusao_12_43', 'Fusao_13_44', 'Fusao_14_45',
        'Fusao_15_46', 'Fusao_16_47', 'Fusao_17_48', 'Fusao_18_49'],
       dtype='object'),
 51)

In [229]:
df_deduplicado.rename(columns={
    
    '0': 'Carimbo de data/hora',
    '1': 'Endereço de e-mail',
    '2': 'Qual é a sua idade?',
    '3': 'Gênero',
    '4': 'Quais plataformas de mídia social você costuma usar?',
    '5': 'Cidade onde Mora',
    '6': 'Sexo',
    '7': 'Está empregado',
    '19': 'Qual sua renda mensal bruta para custo de vida',
    '20': 'Você têm religião?',
    '21': 'Qual sua religião?',
    '22': 'Qual é o tempo médio que você passa nas redes sociais todos os dias em horas?',
    '23': 'Numa escala de 1 a 5, quão facilmente você se distrai?  (Sendo 1 pouco e 5 muito)  ',
    '24': 'Você acha difícil se concentrar nas coisas?    ',
    '25': 'Pratica esporte com que frequência mensal?',
    '26': 'Com que frequência você se distrai com as redes sociais quando está ocupado fazendo alguma coisa?',
    '27': 'Com que frequência você se sente deprimido ou está deprimido?    ',
    '28': 'Com que frequência você usa mídias sociais sem um propósito específico?',
    '29': 'Numa escala de 1 a 5, com que frequência você se compara a outras pessoas de sucesso através do uso das redes sociais?',
    '30': 'Como você se sente quando vê publicações de pessoas mostrando vidas aparentemente perfeitas?',
    '31': 'Como você se sente ao receber poucos "likes" em suas postagens?',
    '32': 'Você sente que o uso das redes sociais impacta seu humor de forma positiva ou negativa?',
    '33': 'Dificuldade para dormir',
    '34': 'Qual o impacto que você acredita que as redes sociais causam em você? (sendo 1 muito negativo e 5 muito positivo )',
    '35': 'Você acha que passa mais tempo nas redes sociais do que gostaria? ',
    '36': 'Como você reage quando vê comentários negativos ou críticas em suas postagens?',
    '37': 'Com que frequência você busca validação por meio de "curtidas" ou outros recursos das redes sociais?',
    '38': 'Com que frequência você usa mídias sociais sem um propósito específico? ',
    '39': 'Você já experimentou sentimentos de inveja ou inferioridade ao se comparar com outras pessoas nas redes? (Ex.: Aquele momento em que você abre a rede social do amigo e pensa dei errado para caramba)',
    '8': 'Fusao_8_50',
    '9': 'Fusao_9_40',
    '10': 'Fusao_10_41',
    '11': 'Fusao_11_42',
    '12': 'Fusao_12_43',
    '13': 'Fusao_13_44',
    '14': 'Fusao_14_45',
    '15': 'Fusao_15_46',
    '16': 'Fusao_16_47',
    '17': 'Fusao_17_48',
    '18': 'Fusao_18_49'
}, inplace=True)


In [239]:
# df_deduplicado.to_csv("datasetPesquisaTratado_ritulosExplicitos.csv")

In [231]:
df_deduplicado.keys()

Index(['Carimbo de data/hora', 'Endereço de e-mail', 'Qual é a sua idade?',
       'Gênero', 'Quais plataformas de mídia social você costuma usar?',
       'Cidade onde Mora', 'Sexo', 'Está empregado',
       'Qual sua renda mensal bruta para custo de vida', 'Você têm religião?',
       'Qual sua religião?',
       'Qual é o tempo médio que você passa nas redes sociais todos os dias em horas?',
       'Numa escala de 1 a 5, quão facilmente você se distrai?  (Sendo 1 pouco e 5 muito)  ',
       'Você acha difícil se concentrar nas coisas?    ',
       'Pratica esporte com que frequência mensal?',
       'Com que frequência você se distrai com as redes sociais quando está ocupado fazendo alguma coisa?',
       'Com que frequência você se sente deprimido ou está deprimido?    ',
       'Com que frequência você usa mídias sociais sem um propósito específico?',
       'Numa escala de 1 a 5, com que frequência você se compara a outras pessoas de sucesso através do uso das redes sociais?',
  

In [233]:
perfilamento = ProfileReport(df_deduplicado, title="Perfilamento e EDA")

In [235]:
perfilamento.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]